In [2]:
import pandas as pd
import numpy as np

In [23]:
df = pd.read_csv('linearRawData.csv')

In [3]:
df

Unnamed: 0  feature1      target
0                0 -0.445142   23.136758
1                1  0.072545  118.460441
2                2 -1.366360 -119.291554
3                3  0.065654 -161.423879
4                4 -0.321074 -158.935795
...            ...       ...         ...
999995      999995 -1.658399  -16.952064
999996      999996  1.306171   99.958785
999997      999997 -1.487774  -54.165296
999998      999998  0.009367   61.062049
999999      999999 -1.279103  -77.098384

[1000000 rows x 3 columns]

In [4]:
df.drop('Unnamed: 0', axis=1, inplace=True)

In [38]:
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error, r2_score

features = df[['feature1']]
target = df['target']

x_train, x_test, y_train, y_test = train_test_split(features, target, test_size=0.2, random_state=0)

model = LinearRegression()
model.fit(x_train, y_train)

y_pred = model.predict(x_test)

mse = mean_squared_error(y_test, y_pred)
r2 = r2_score(y_test, y_pred)

residuals = y_test - y_pred
residual_variance = np.var(residuals)

print(f'Mean squared error: {mse}')
print(f'Residual: {residual_variance}')
print(f'r2 score: {r2}')

Mean squared error: 10773.590011965625
Residual: 10773.585054050001
r2 score: 0.08922805459225014


In [ ]:
import matplotlib.pyplot as plt
import matplotlib as mpl

mpl.rcParams['agg.path.chunksize'] = 1000
mpl.rcParams['path.simplify_threshold'] = 0.1

def plot_feature_vs_target(feature, target):
    fig, ax = plt.subplots()
    ax.plot(feature, target, marker='o', linestyle='--', label='Feature vs Target')
    ax.set_xlabel('Feature')
    ax.set_ylabel('Target')
    ax.set_title('Feature vs Target Line Graph')
    plt.show()

plot_feature_vs_target(x_train, y_train)

In [37]:
x_col = ("feature1")
y_col = ("target")

plt.figure(figsize=(100,100)) # set the figure size
plt.scatter(df[x_col], df[y_col])
plt.xlabel(x_col)
plt.ylabel(y_col)
plt.title('Scatter Plot of {} vs. {}'.format(x_col, y_col))
plt.show()

In [ ]:
from sklearn.cluster import DBSCAN

eps = 0.5
minSamples = 5

X = df[['feature1']].values  # assuming 'feature1' is the column of interest
dbscan = DBSCAN(eps=eps, min_samples=minSamples)
dbscan.fit(X)

labels = dbscan.labels_
n_clusters = len(set(labels)) - (1 if -1 in labels else 0)
df_no_outliers = df[labels != -1]

In [5]:
# Define the number of sub-DataFrames you want to create
n_sub_dfs = 5

# Calculate the size of each sub-DataFrame
sub_df_size = len(df) // n_sub_dfs

# Create the sub-DataFrames
sub_dfs = []
for i in range(n_sub_dfs):
    start_index = i * sub_df_size
    end_index = (i + 1) * sub_df_size
    if i == n_sub_dfs - 1:
        end_index = len(df)
    sub_dfs.append(df.iloc[start_index:end_index])

In [6]:
df_cp = sub_dfs[0]

In [ ]:
# from sklearn.cluster import DBSCAN
# 
# eps = 0.5
# minSamples = 5
# 
# X = df_cp[['feature1']].values  # assuming 'feature1' is the column of interest
# dbscan = DBSCAN(eps=eps, min_samples=minSamples)
# dbscan.fit(X)
# 
# labels = dbscan.labels_
# n_clusters = len(set(labels)) - (1 if -1 in labels else 0)
# df_no_outliers = df[labels != -1]

In [20]:
import numpy as np
from sklearn.ensemble import IsolationForest

# Assume `df` is your DataFrame with 1000000 values
# and `feature1` is the column of interest

X = df['feature1'].values.reshape(-1, 1)

# Define Isolation Forest parameters
n_estimators = 100
contamination = 0.5

# Train the Isolation Forest model
isolation_forest = IsolationForest(random_state=0, n_estimators=n_estimators, contamination=contamination)
isolation_forest.fit(X)

# Predict the anomaly score for each data point
scores = isolation_forest.decision_function(X)

# Define the threshold for outliers
outlier_threshold = np.percentile(scores, 100 * contamination)

# Identify the indices of the outliers
outliers = np.where(scores < outlier_threshold)

# Remove the outliers
df_no_outliers = df.iloc[np.delete(np.arange(len(df)), outliers)]

In [21]:
df

feature1      target
0      -0.445142   23.136758
1       0.072545  118.460441
2      -1.366360 -119.291554
3       0.065654 -161.423879
4      -0.321074 -158.935795
...          ...         ...
999995 -1.658399  -16.952064
999996  1.306171   99.958785
999997 -1.487774  -54.165296
999998  0.009367   61.062049
999999 -1.279103  -77.098384

[1000000 rows x 2 columns]

In [36]:
from scipy.stats import zscore

z_scores = np.abs(zscore(df['feature1']))

# Set a threshold for identifying outliers based on Z-score
z_threshold = 1
outliers_z = np.where(z_scores > z_threshold)

# Calculate the IQR of the 'feature1' column
iqr = df['feature1'].quantile(0.75) - df['feature1'].quantile(0.25)

# Set a threshold for identifying outliers based on IQR
iqr_threshold = 1.0
outliers_iqr = np.where((df['feature1'] > df['feature1'].quantile(0.75) + iqr_threshold * iqr) | (df['feature1'] < df['feature1'].quantile(0.25) - iqr_threshold * iqr))

# Identify and remove outliers based on both Z-score and IQR methods
outliers = np.union1d(outliers_z[0], outliers_iqr[0])
df_no_outliers = df.drop(outliers)

df_no_outliers

Unnamed: 0  feature1      target
0                0 -0.445142   23.136758
1                1  0.072545  118.460441
3                3  0.065654 -161.423879
4                4 -0.321074 -158.935795
5                5 -0.659159 -157.068259
...            ...       ...         ...
999990      999990  0.512121  -17.532236
999991      999991 -0.001784  238.089327
999992      999992  0.554015   86.945127
999993      999993  0.539150  -67.277491
999998      999998  0.009367   61.062049

[682768 rows x 3 columns]